In [2]:
#!pip install bs4
import requests
from bs4 import BeautifulSoup
import pandas as pd

C:\Users\Siloux\.conda\envs\species-id\lib\site-packages\bs4\element.py:16: UserWarning: The soupsieve package is not installed. CSS selectors cannot be used.
  'The soupsieve package is not installed. CSS selectors cannot be used.'


In [3]:
def get_species_list(num_species=-1):
    #print("getting species list")
    #get page of all xento-canto species
    url = 'https://xeno-canto.org/collection/species/all'
    page = requests.get(url)
    soup = BeautifulSoup(page.text, 'lxml')
    species_table = soup.find_all("table", {"class": "results"})[0]
    
    #get headers of table
    headers = []
    for i in species_table.find_all('thead'):
         title = i.text
         headers.append(title)
    headers = headers[0].strip().split("\n")
    
    #add header for url and create DF
    headers.append('url')
    species_list = pd.DataFrame(columns = headers)
    
    #Get data from each row
    for j in species_table.find_all('tr'):
         #get row data
         row_data = j.find_all('td')
        
         #get all text from row
         row = [i.text for i in row_data]
        
         #get the link
         row.append(row_data[0].a["href"])
        
         #add to dataframe
         length = len(species_list)
         species_list.loc[length] = row

    #Decide to return full list or do RS     
    if (num_species == -1 or num_species > species_list.shape[0]):
        return species_list
    return species_list.sample(num_species).reset_index(drop=True)

#get_species_list()
#test1 = get_species_list(5)
#test1

In [4]:
def get_species_data(link_to_XC):
    #print("getting species file metadata for: " + link_to_XC)
    #get soup for Species
    url = 'https://xeno-canto.org' + link_to_XC
    page = requests.get(url)
    soup = BeautifulSoup(page.text, 'lxml')
    species_table = soup.find_all("table", {"class": "results"})[0]
    
    # Obtain every title of columns with tag <th>
    headers = []
    for i in species_table.find_all('thead'):
     title = i.text
     headers.append(title)

    headers = headers[0].strip()
    headers = headers.split("\n")
    headers[1] = "Common name / Scientific"
    headers.append("copyright")
    headers.append("filename")
    headers.append("download url")


    species_list = pd.DataFrame(columns = headers[1:])
    
    
    page_count = 1
    while len(species_table.find_all('tr')) != 1:
        
        #print(len(species_table.find_all('tr')))
        
        #Get data from each row
        for j in species_table.find_all('tr'):
            #get row data
            row_data = j.find_all('td')

            if (row_data == []):
                   continue

            #print(row_data) 
            #get all text from row
            row = [i.text.strip() for i in row_data][1:]

            #get copyright, download link and filename
            copyright = row_data[12].a.span["title"]
            try:
                 filename = row_data[11].a["download"]
            except:
                filename = "PROTECTED SPECIES"
            download_url = row_data[11].a["href"]
            row.append(copyright)
            row.append(filename)
            row.append(download_url)

            #add to dataframe
            length = len(species_list)
            species_list.loc[length] = row
        
        ## Get data for next page of audio data
        page_count += 1
        url = 'https://xeno-canto.org' + link_to_XC + "?pg=" + str(page_count)
        page = requests.get(url)
        soup = BeautifulSoup(page.text, 'lxml')
        species_table = soup.find_all("table", {"class": "results"})[0]
    return species_list

#test2 = get_species_data(test1.iloc[0]["url"])
#test2

In [5]:
all_species = get_species_list()

In [6]:
nips_birds = pd.read_csv("./nips/nips4b_birdchallenge_espece_list.csv")

In [7]:
species_list = all_species.merge(nips_birds.groupby("Scientific_name").count(), left_on="Scientific name", right_index=True)

In [8]:
species_list.shape

(49, 10)

In [9]:
species_list = all_species.merge(nips_birds.groupby("Scientific_name").count(), left_on="Scientific name", right_index=True)

In [10]:
species_list.groupby("Scientific name").count().shape

(49, 9)

In [11]:
nips_birds.groupby("Scientific_name")

In [12]:
nips_birds[~nips_birds["Scientific_name"].isin(species_list["Scientific name"])]

class number   class name          English_name         Scientific_name  \
0          none        Empty                 Empty            noise sample   
13           13  Cicatr_song          Black Cicada          Cicadatra atra   
14           14  Cicorn_song           Grey Cicada             Cicada orni   
35           35  Lularb_song              Woodlark         lullula arborea   
38           38  Lyrple_song         Common Cicada       Lyristes plebejus   
50           50  Pelgra_call    Graf's Hybrid Frog    Pelophylax kl. grafi   
53           53  Phofem_song   Fallow Bush-cricket   Pholidoptera femorata   
57           57  Plaaff_song  Coastal Bush-cricket      Platycleis affinis   
58           58  Plasab_song     Sand Bush-Cricket     Platycleis sabulosa   
62           62  Ptehey_song         Marsh Cricket  Pteronemobius heydenii   
64           64  Regign_call      Common Firecrest    Regulus ignicapillus   
65           65  Regign_song      Common Firecrest    Regulus ignicapillus   
81           81  Tetpyg_song          Pygmy Cicada     Tettigettula pygmea   
82           82  Tibtom_song      Tomentous Cicada      Tibicina tomentosa   

         type  
0       noise  
13     insect  
14     insect  
35       bird  
38     insect  
50  amphibian  
53     insect  
57     insect  
58     insect  
62     insect  
64       bird  
65       bird  
81     insect  
82     insect

In [13]:
species_list

Common name          Scientific name Status   No.  \
1369         \n\nCommon Wood Pigeon\n\n         Columba palumbus          693   
1416       \n\nEuropean Turtle Dove\n\n      Streptopelia turtur          339   
1421     \n\nEurasian Collared Dove\n\n    Streptopelia decaocto          832   
2948             \n\nCommon Buzzard\n\n              Buteo buteo          824   
3715           \n\nEurasian Wryneck\n\n           Jynx torquilla          535   
3855   \n\nGreat Spotted Woodpecker\n\n        Dendrocopos major         2178   
6607     \n\nEurasian Golden Oriole\n\n          Oriolus oriolus         1140   
6837               \n\nEurasian Jay\n\n      Garrulus glandarius         1705   
6861            \n\nEurasian Magpie\n\n                Pica pica         1029   
6907               \n\nCarrion Crow\n\n            Corvus corone         1453   
7058                   \n\nCoal Tit\n\n           Periparus ater         2375   
7062       \n\nEuropean Crested Tit\n\n    Lophophanes cristatus          841   
7085                  \n\nMarsh Tit\n\n        Poecile palustris         1278   
7090          \n\nEurasian Blue Tit\n\n      Cyanistes caeruleus         3893   
7093                  \n\nGreat Tit\n\n              Parus major         6888   
7202           \n\nEurasian Skylark\n\n          Alauda arvensis         2204   
7206              \n\nThekla's Lark\n\n         Galerida theklae          238   
7207               \n\nCrested Lark\n\n        Galerida cristata          463   
7430               \n\nBarn Swallow\n\n          Hirundo rustica         1554   
7518            \n\nCetti's Warbler\n\n             Cettia cetti         1405   
7533            \n\nLong-tailed Tit\n\n      Aegithalos caudatus         1541   
7572          \n\nCommon Chiffchaff\n\n   Phylloscopus collybita         5101   
7806          \n\nZitting Cisticola\n\n       Cisticola juncidis          799   
8189          \n\nEurasian Blackcap\n\n       Sylvia atricapilla         4219   
8201           \n\nDartford Warbler\n\n            Sylvia undata          337   
8206          \n\nSubalpine Warbler\n\n        Sylvia cantillans          475   
8208          \n\nSardinian Warbler\n\n     Sylvia melanocephala         1160   
8475              \n\nEurasian Wren\n\n  Troglodytes troglodytes         3636   
8521          \n\nEurasian Nuthatch\n\n           Sitta europaea         1696   
8553     \n\nShort-toed Treecreeper\n\n    Certhia brachydactyla         1105   
8665            \n\nCommon Starling\n\n         Sturnus vulgaris         1504   
8825           \n\nCommon Blackbird\n\n            Turdus merula         5962   
8843                \n\nSong Thrush\n\n        Turdus philomelos         4245   
8933         \n\nSpotted Flycatcher\n\n        Muscicapa striata         1121   
9007             \n\nEuropean Robin\n\n       Erithacus rubecula         4730   
9065         \n\nCommon Nightingale\n\n    Luscinia megarhynchos         2094   
9435              \n\nHouse Sparrow\n\n        Passer domesticus         2282   
9463               \n\nRock Sparrow\n\n        Petronia petronia          230   
9765                    \n\nDunnock\n\n       Prunella modularis         2045   
9775               \n\nGrey Wagtail\n\n        Motacilla cinerea          725   
9806                 \n\nTree Pipit\n\n         Anthus trivialis         1732   
9838           \n\nCommon Chaffinch\n\n        Fringilla coelebs         5648   
9857         \n\nEurasian Bullfinch\n\n        Pyrrhula pyrrhula         1341   
9942        \n\nEuropean Greenfinch\n\n          Chloris chloris         1861   
9990              \n\nCommon Linnet\n\n        Linaria cannabina         1403   
9998              \n\nRed Crossbill\n\n        Loxia curvirostra         4038   
10003        \n\nEuropean Goldfinch\n\n      Carduelis carduelis         1846   
10007            \n\nEuropean Serin\n\n          Serinus serinus         1168   
10087              \n\nCirl Bunting\n\n          Emberiza c

In [14]:
#file_meta = download_xento_canto_data(-1, -1, "./nips/data/", species_list=species_list)
#file_meta.to_csv("./nips/meta.csv")

In [15]:
def download_data(species_df, num_of_files, download_folder):
    #print("downloading data")
    if (num_of_files != -1 and species_df.shape[0] > num_of_files):
        species_df = species_df.sample(num_of_files, replace=False)
    species_df["file_location"] = species_df[["filename","download url"]].apply(download_by_url,axis=1, args=(tuple([download_folder])))
    return species_df

#download_data(test2, 100, "./data/")

In [16]:
def download_xento_canto_data(num_species, num_of_files, download_folder, species_list=pd.DataFrame()):
    file_df = pd.DataFrame()
    if (species_list.empty):
        species_list = get_species_list(num_species)
    for url in species_list["url"]:
        try:
            species_files = get_species_data(url)
            temp_file_df = download_data(species_files, num_of_files, download_folder)
            if (file_df.empty):
                file_df = temp_file_df.reset_index(drop=True)
            else:
                file_df = file_df.append(temp_file_df.reset_index(drop=True)).reset_index(drop=True)
        except Exception as e:
            print(url + " did not download")
            print(e)
    return file_df
        

In [17]:
from tqdm import tqdm
file_df = pd.DataFrame()
for url in tqdm(species_list["url"]):
    try:
        species_files = get_species_data(url)
        #species_files = species_files[species_files["Length"][0] == 0]
        #print(species_files)
        #species_files = download_data(species_files, -1, "./nips/data/")
        print(species_files)
        #species_files = download_by_url(file_data, download_folder)
    except Exception as e:
        print(e)
        continue
    if (file_df.empty):
        file_df = species_files.reset_index(drop=True)
    else:
        file_df = file_df.append(species_files.reset_index(drop=True)).reset_index(drop=True)
file_df

  2%|█▋                                                                                 | 1/49 [00:42<33:48, 42.26s/it]

                  Common name / Scientific Length       Recordist        Date  \
0    Common Wood Pigeon (Columba palumbus)   0:23  Oscar Campbell  2022-07-27   
1    Common Wood Pigeon (Columba palumbus)   2:01    Lars Edenius  2022-07-29   
2    Common Wood Pigeon (Columba palumbus)   0:41   Craig Brookes  2020-08-07   
3    Common Wood Pigeon (Columba palumbus)   0:11    Jorge Leitão  2022-08-08   
4    Common Wood Pigeon (Columba palumbus)   1:55    Lars Edenius  2022-07-28   
..                                     ...    ...             ...         ...   
691  Common Wood Pigeon (Columba palumbus)   0:59         david m  2014-01-16   
692  Common Wood Pigeon (Columba palumbus)   0:20         david m  2015-11-22   
693  Common Wood Pigeon (Columba palumbus)   0:26         david m  2011-12-24   
694  Common Wood Pigeon (Columba palumbus)   0:21         david m  2015-03-12   
695  Common Wood Pigeon (Columba palumbus)   0:20     Bob Planqué  2009-07-10   

      Time         Country 

  4%|███▍                                                                               | 2/49 [00:53<18:56, 24.19s/it]

                              Common name / Scientific Length  \
0           European Turtle Dove (Streptopelia turtur)   0:48   
1    European Turtle Dove (Streptopelia turtur turtur)   1:30   
2           European Turtle Dove (Streptopelia turtur)   0:19   
3           European Turtle Dove (Streptopelia turtur)   0:14   
4           European Turtle Dove (Streptopelia turtur)   0:27   
..                                                 ...    ...   
334         European Turtle Dove (Streptopelia turtur)   0:17   
335  European Turtle Dove (Streptopelia turtur turtur)   0:13   
336         European Turtle Dove (Streptopelia turtur)   0:14   
337         European Turtle Dove (Streptopelia turtur)   0:19   
338         European Turtle Dove (Streptopelia turtur)   0:32   

                   Recordist        Date    Time         Country  \
0             Bastian Forkel  2022-08-11   10:30         Germany   
1              Frank Lambert  2022-05-29   20:31  United Kingdom   
2    Jacobo Ram

  6%|█████                                                                              | 3/49 [01:32<23:33, 30.73s/it]

...

 78%|█████████████████████████████████████████████████████████████▎                 | 38/49 [1:15:32<22:31, 122.90s/it]

             Common name / Scientific Length            Recordist        Date  \
0    Rock Sparrow (Petronia petronia)   0:08   Testaert Dominique  2020-06-10   
1    Rock Sparrow (Petronia petronia)   0:11   Testaert Dominique  2020-06-10   
2    Rock Sparrow (Petronia petronia)   0:10   Testaert Dominique  2020-06-10   
3    Rock Sparrow (Petronia petronia)   0:20       Gianluca Congi  2022-04-15   
4    Rock Sparrow (Petronia petronia)   0:16  JOSE IGNACIO MOLINA  2022-04-10   
..                                ...    ...                  ...         ...   
225  Rock Sparrow (Petronia petronia)   0:04       Cedric Mroczko  2020-12-18   
226  Rock Sparrow (Petronia petronia)   0:11   Philippe J. DUBOIS  2019-07-15   
227  Rock Sparrow (Petronia petronia)   0:08       Cedric Mroczko  2017-06-26   
228  Rock Sparrow (Petronia petronia)   0:52        Simona Inaudi  2014-08-16   
229  Rock Sparrow (Petronia petronia)   0:10         Egidio Fulco  2009-06-10   

      Time   Country       

100%|███████████████████████████████████████████████████████████████████████████████| 49/49 [1:22:17<00:00, 100.77s/it]

("Connection broken: ConnectionAbortedError(10053, 'An established connection was aborted by the software in your host machine', None, 10053, None)", ConnectionAbortedError(10053, 'An established connection was aborted by the software in your host machine', None, 10053, None))
HTTPSConnectionPool(host='xeno-canto.org', port=443): Max retries exceeded with url: /species/Motacilla-cinerea (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x000002620CBD6B48>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPSConnectionPool(host='xeno-canto.org', port=443): Max retries exceeded with url: /species/Anthus-trivialis (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x0000026210C8B788>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
HTTPSConnectionPool(host='xeno-canto.org', port=443): Max retries exceeded with url: /species/Fringilla-coelebs (Caused by NewConnectionError('<urllib3.con

Common name / Scientific Length           Recordist  \
0      Common Wood Pigeon (Columba palumbus)   0:23      Oscar Campbell   
1      Common Wood Pigeon (Columba palumbus)   2:01        Lars Edenius   
2      Common Wood Pigeon (Columba palumbus)   0:41       Craig Brookes   
3      Common Wood Pigeon (Columba palumbus)   0:11        Jorge Leitão   
4      Common Wood Pigeon (Columba palumbus)   1:55        Lars Edenius   
...                                      ...    ...                 ...   
74114       Rock Sparrow (Petronia petronia)   0:04      Cedric Mroczko   
74115       Rock Sparrow (Petronia petronia)   0:11  Philippe J. DUBOIS   
74116       Rock Sparrow (Petronia petronia)   0:08      Cedric Mroczko   
74117       Rock Sparrow (Petronia petronia)   0:52       Simona Inaudi   
74118       Rock Sparrow (Petronia petronia)   0:10        Egidio Fulco   

             Date   Time         Country  \
0      2022-07-27  07:30        Portugal   
1      2022-07-29  04:00          Sweden   
2      2020-08-07  06:30  United Kingdom   
3      2022-08-08  19:07        Portugal   
4      2022-07-28  04:00          Sweden   
...           ...    ...             ...   
74114  2020-12-18  17:00          Turkey   
74115  2019-07-15  14:00        Mongolia   
74116  2017-06-26  20:15          France   
74117  2014-08-16  07:30           Italy   
74118  2009-06-10  10:15           Italy   

                                                Location Elev. (m)  \
0                           Pico da Vigia, Santa Barbara       120   
1                        Kåddis, Umeå, Västerbottens län        60   
2      The Quarry (near  Dursley), Gloucestershire, E...        90   
3          Estuário do Âncora, Caminha, Viana do Castelo         0   
4                        Kåddis, Umeå, Västerbottens län        60   
...                                                  ...       ...   
74114                 Kapıkaya kanyonu, Karaisalı, Adana       170   
74115                       Yahii Nuur, Sergelen, Dornod       650   
74116                        Cestayrols, Tarn, Occitanie       260   
74117                         Matera, Matera, Basilicata       400   
74118                            San Martino d'Agri (PZ)       700   

                             Type  \
0      adult, sex uncertain, song   
1                            song   
2               adult, male, song   
3                            call   
4                            song   
...                           ...   
74114                  alarm call   
74115                 flight call   
74116                 flight call   
74117        passer italiae, song   
74118                        Song   

                                                 Remarks Actions   Cat.nr.  \
0      Song of bird, not seen, in dense forest.\nbird...   ABCDE  XC744882   
1      Unattended recording\nbird-seen:no\nplayback-u...   ABCDE  XC742898   
2       bird-seen:no\nplayback-used:no\n  [also]\n[sono]   ABCDE  XC742189   
3               bird-seen:yes\nplayback-used:no\n [sono]   ABCDE  XC742088   
4      Unattended recording\nbird-seen:no\nplayback-u...   ABCDE  XC741277   
...                                                  ...     ...       ...   
74114  High-pass filtered (1000Hz, 6dB)\nbird-seen:ye...   ABCDE  XC611660   
74115  flight calls of a large group\nbird-seen:yes\n...   ABCDE  XC491983   
74116  Also Sepiana sepium bushcricket and Eumodicogr...   ABCDE  XC396981   
74117           bird-seen:yes\nplayback-used:no\n [sono]   ABCDE  XC193213   
74118                                     [also]\n[sono]   ABCDE  XC101021   

                                               copyright  \
0      Creative Commons Attribution-NonCommercial-NoD...   
1      Creative Commons Attribution-NonCommercial-Sha...   
2      Creative Commons Attribution-NonCommercial-Sha...   
3      Creative Commons Attribution-NonCommercial-Sha...   
4      Creative Commons Attribution-NonCommercial-Sha...   
...    

In [18]:
import numpy as np
species_to_focus_on = np.array(file_df.groupby("Common name / Scientific").count().sort_values("Length", ascending=False).head(15).index)
mini_file_df = file_df[file_df["Common name / Scientific"].isin(species_to_focus_on)].reset_index(drop=True)
mini_file_df

Common name / Scientific Length          Recordist  \
0      Great Spotted Woodpecker (Dendrocopos major)   0:11       Lars Edenius   
1      Great Spotted Woodpecker (Dendrocopos major)   0:25    Romuald Mikusek   
2      Great Spotted Woodpecker (Dendrocopos major)   0:03     Martin Billard   
3      Great Spotted Woodpecker (Dendrocopos major)   0:06        Rob Olivier   
4      Great Spotted Woodpecker (Dendrocopos major)   0:28    Romuald Mikusek   
...                                             ...    ...                ...   
43205             House Sparrow (Passer domesticus)   0:07  Piotr Szczypinski   
43206             House Sparrow (Passer domesticus)   0:46          Ted Floyd   
43207             House Sparrow (Passer domesticus)   0:26     Joss Deffarges   
43208             House Sparrow (Passer domesticus)   1:28            david m   
43209             House Sparrow (Passer domesticus)   1:04      Paweł Malczyk   

             Date   Time         Country  \
0      2022-08-24  06:30          Sweden   
1      2022-06-10  18:00          Poland   
2      2022-08-18  00:20          France   
3      2022-08-12  07:34     Netherlands   
4      2022-04-28  10:30          Poland   
...           ...    ...             ...   
43205  2018-10-10  09:30          Poland   
43206  2017-11-20  06:58   United States   
43207  2010-12-21  21:46     New Zealand   
43208  2014-11-11  08:17  United Kingdom   
43209  2014-04-29  07:00          Poland   

                                                Location Elev. (m)  \
0                        Kåddis, Umeå, Västerbottens län        60   
1               Noteć Forest, Greater Poland Voivodeship        70   
2      Arrondissement de Caen (near  Feuguerolles-Bul...        60   
3                         Ulrum, Het Hogeland, Groningen         0   
4          Sobibór Forest, Włodawa, włodawski, lubelskie       170   
...                                                  ...       ...   
43205    Gmina Dzierzgowo, nidzicki, warmińsko-mazurskie       130   
43206                       Lafayette, Boulder, Colorado      1600   
43207  Cape Palliser, South Wairarapa District, Welli...        10   
43208  Waveney District (near  Southwold), Suffolk, E...         0   
43209  Gmina Trzebinia, Chrzanów County, Lesser Polan...       420   

                                     Type  \
0                                    call   
1                     call, sex uncertain   
2      flight call, nocturnal flight call   
3                                    call   
4           call, drumming, sex uncertain   
...                                   ...   
43205                         flight call   
43206                                call   
43207                          call, song   
43208                  call, female, male   
43209                                call   

                                                 Remarks Actions   Cat.nr.  \
0      Unattended recording\nbird-seen:no\nplayback-u...   ABCDE  XC745626   
1      open area with rare bushes & trees\nbird-seen:...   ABCDE  XC743899   
2      First time for me during an NFC recording\nbir...   ABCDE  XC743775   
3                bird-seen:no\nplayback-used:no\n [sono]   ABCDE  XC742709   
4      pine forest with bogs around\nbird-seen:no\npl...   ABCDE  XC742680   
...                                                  ...     ...       ...   
43205  A bird in flight, in a river valley.\nbird-see...   ABCDE  XC437906   
43206  (Note:  Bird unseen, because it was in a shrub...   ABCDE  XC393851   
43207  filtering soundforge\nplayback-used:no\n  [als...   ABCDE  XC309048   
43208  House sparrow  call ... not filtered ... parab...   ABCDE  XC215694   
43209  bird-seen:yes\nplayback-used:no\n  [also]\n[sono]   ABCDE  XC176545   

                                               copyright  \
0      Creative Commons Attribution-NonCommercial-Sha...   
1      Creative Commons Attribution-NonCommercial-Sha...   
2      Creative Commons At

In [22]:
import os
from requests.exceptions import Timeout
def download_by_url(file_data, download_folder):
    url = file_data["download url"]
    url = 'https://xeno-canto.org' + url
    path = download_folder+file_data["filename"]
    if (os.path.exists(path)):
        return path
    try:
        r = requests.get(url, timeout=100)
        open(path, "wb").write(r.content)
    except Timeout: 
        path = "TIMEOUT"
    except Exception as e:
        print(e)
        path="ERROR"
    return path

In [25]:
from tqdm import tqdm
from time import sleep
for i, row in tqdm(mini_file_df.iterrows()):
    try:
        row["download_path"] = download_by_url(row, "./nips/data/")
        mini_file_df.loc[i] = row
    except Exception as e:
        print("========================")
        print(e)
        continue
mini_file_df

9915it [01:59,  3.39it/s] 

HTTPSConnectionPool(host='xeno-canto.org', port=443): Read timed out.


21736it [04:20,  3.80it/s] 

HTTPSConnectionPool(host='xeno-canto.org', port=443): Read timed out.


27821it [07:02,  1.18it/s] 

...

43209it [9:15:35,  1.78s/it]

[Errno 28] No space left on device


43210it [9:15:37,  1.30it/s]

[Errno 28] No space left on device


Common name / Scientific Length          Recordist  \
0      Great Spotted Woodpecker (Dendrocopos major)   0:11       Lars Edenius   
1      Great Spotted Woodpecker (Dendrocopos major)   0:25    Romuald Mikusek   
2      Great Spotted Woodpecker (Dendrocopos major)   0:03     Martin Billard   
3      Great Spotted Woodpecker (Dendrocopos major)   0:06        Rob Olivier   
4      Great Spotted Woodpecker (Dendrocopos major)   0:28    Romuald Mikusek   
...                                             ...    ...                ...   
43205             House Sparrow (Passer domesticus)   0:07  Piotr Szczypinski   
43206             House Sparrow (Passer domesticus)   0:46          Ted Floyd   
43207             House Sparrow (Passer domesticus)   0:26     Joss Deffarges   
43208             House Sparrow (Passer domesticus)   1:28            david m   
43209             House Sparrow (Passer domesticus)   1:04      Paweł Malczyk   

             Date   Time         Country  \
0      2022-08-24  06:30          Sweden   
1      2022-06-10  18:00          Poland   
2      2022-08-18  00:20          France   
3      2022-08-12  07:34     Netherlands   
4      2022-04-28  10:30          Poland   
...           ...    ...             ...   
43205  2018-10-10  09:30          Poland   
43206  2017-11-20  06:58   United States   
43207  2010-12-21  21:46     New Zealand   
43208  2014-11-11  08:17  United Kingdom   
43209  2014-04-29  07:00          Poland   

                                                Location Elev. (m)  \
0                        Kåddis, Umeå, Västerbottens län        60   
1               Noteć Forest, Greater Poland Voivodeship        70   
2      Arrondissement de Caen (near  Feuguerolles-Bul...        60   
3                         Ulrum, Het Hogeland, Groningen         0   
4          Sobibór Forest, Włodawa, włodawski, lubelskie       170   
...                                                  ...       ...   
43205    Gmina Dzierzgowo, nidzicki, warmińsko-mazurskie       130   
43206                       Lafayette, Boulder, Colorado      1600   
43207  Cape Palliser, South Wairarapa District, Welli...        10   
43208  Waveney District (near  Southwold), Suffolk, E...         0   
43209  Gmina Trzebinia, Chrzanów County, Lesser Polan...       420   

                                     Type  \
0                                    call   
1                     call, sex uncertain   
2      flight call, nocturnal flight call   
3                                    call   
4           call, drumming, sex uncertain   
...                                   ...   
43205                         flight call   
43206                                call   
43207                          call, song   
43208                  call, female, male   
43209                                call   

                                                 Remarks Actions   Cat.nr.  \
0      Unattended recording\nbird-seen:no\nplayback-u...   ABCDE  XC745626   
1      open area with rare bushes & trees\nbird-seen:...   ABCDE  XC743899   
2      First time for me during an NFC recording\nbir...   ABCDE  XC743775   
3                bird-seen:no\nplayback-used:no\n [sono]   ABCDE  XC742709   
4      pine forest with bogs around\nbird-seen:no\npl...   ABCDE  XC742680   
...                                                  ...     ...       ...   
43205  A bird in flight, in a river valley.\nbird-see...   ABCDE  XC437906   
43206  (Note:  Bird unseen, because it was in a shrub...   ABCDE  XC393851   
43207  filtering soundforge\nplayback-used:no\n  [als...   ABCDE  XC309048   
43208  House sparrow  call ... not filtered ... parab...   ABCDE  XC215694   
43209  bird-seen:yes\nplayback-used:no\n  [also]\n[sono]   ABCDE  XC176545   

                                               copyright  \
0      Creative Commons Attribution-NonCommercial-Sha...   
1      Creative Commons Attribution-NonCommercial-Sha...   
2      Creative Commons At

In [21]:
mini_file_df.to_csv("metadata")

In [27]:
mini_file_df["DONE"] = False

In [28]:
import glob
import os
dir_name = './nips/data/'
# Get a list of files (file paths) in the given directory 
list_of_files = filter( os.path.isfile,
                        glob.glob(dir_name + '/**/*', recursive=True) )
# get list of ffiles with size
files_with_size = [ (file_path, os.stat(file_path).st_size) 
                    for file_path in list_of_files ]
# Iterate over list of tuples i.e. file_paths with size
# and print them one by one


303350  --> ./nips/data\XC100106 - Eurasian Blackcap - Sylvia atricapilla.mp3
303038  --> ./nips/data\XC100109 - Eurasian Blackcap - Sylvia atricapilla.mp3
2606914  --> ./nips/data\XC100117 - House Sparrow - Passer domesticus.mp3
2800492  --> ./nips/data\XC100260 - Song Thrush - Turdus philomelos.mp3
2822114  --> ./nips/data\XC100261 - Eurasian Blackcap - Sylvia atricapilla.mp3
0  --> ./nips/data\XC100311 - Common Nightingale - Luscinia megarhynchos.mp3
410580  --> ./nips/data\XC100329 - Eurasian Nuthatch - Sitta europaea.mp3
480417  --> ./nips/data\XC100473 - Eurasian Jay - Garrulus glandarius.mp3
970113  --> ./nips/data\XC100530 - House Sparrow - Passer domesticus.mp3
588491  --> ./nips/data\XC100531 - House Sparrow - Passer domesticus.mp3
2764071  --> ./nips/data\XC100540 - Song Thrush - Turdus philomelos.mp3
2836876  --> ./nips/data\XC100542 - Common Chiffchaff - Phylloscopus collybita.mp3
3035566  --> ./nips/data\XC100543 - Eurasian Jay - Garrulus glandarius.mp3
0  --> ./nips/data

878205  --> ./nips/data\XC106165 - Common Blackbird - Turdus merula.mp3
0  --> ./nips/data\XC106170 - House Sparrow - Passer domesticus.mp3
244865  --> ./nips/data\XC106175 - House Sparrow - Passer domesticus.mp3
67649  --> ./nips/data\XC106177 - House Sparrow - Passer domesticus.mp3
2670704  --> ./nips/data\XC106531 - Eurasian Wren - Troglodytes troglodytes.mp3
35852  --> ./nips/data\XC106614 - Eurasian Blackcap - Sylvia atricapilla.mp3
46448  --> ./nips/data\XC106680 - Eurasian Nuthatch - Sitta europaea.mp3
31663  --> ./nips/data\XC106706 - Coal Tit - Periparus ater.mp3
939239  --> ./nips/data\XC106756 - Eurasian Jay - Garrulus glandarius.mp3
1455017  --> ./nips/data\XC106782 - Common Blackbird - Turdus merula.mp3
147523  --> ./nips/data\XC106815 - Eurasian Jay - Garrulus glandarius.mp3
155078  --> ./nips/data\XC106839 - Great Spotted Woodpecker - Dendrocopos major.mp3
1193579  --> ./nips/data\XC106940 - Eurasian Skylark - Alauda arvensis.mp3
681488  --> ./nips/data\XC106962 - Great 

357220  --> ./nips/data\XC125029 - Great Spotted Woodpecker - Dendrocopos major.mp3
266592  --> ./nips/data\XC125033 - Eurasian Jay - Garrulus glandarius.mp3
732827  --> ./nips/data\XC125044 - Eurasian Wren - Troglodytes troglodytes.mp3
3505180  --> ./nips/data\XC125115 - Song Thrush - Turdus philomelos.mp3
10030573  --> ./nips/data\XC125118 - Song Thrush - Turdus philomelos.mp3
10036841  --> ./nips/data\XC125120 - Song Thrush - Turdus philomelos.mp3
10034744  --> ./nips/data\XC125122 - Song Thrush - Turdus philomelos.mp3
140713  --> ./nips/data\XC125209 - Common Chiffchaff - Phylloscopus collybita.mp3
893256  --> ./nips/data\XC125415 - Common Chiffchaff - Phylloscopus collybita.mp3
4381897  --> ./nips/data\XC125484 - Great Tit - Parus major.mp3
527158  --> ./nips/data\XC125513 - Eurasian Jay - Garrulus glandarius.mp3
3743002  --> ./nips/data\XC125519 - Great Spotted Woodpecker - Dendrocopos major.mp3
1840514  --> ./nips/data\XC125521 - Great Spotted Woodpecker - Dendrocopos major.mp3


838014  --> ./nips/data\XC129574 - Eurasian Jay - Garrulus glandarius.mp3
441677  --> ./nips/data\XC129575 - Eurasian Jay - Garrulus glandarius.mp3
795037  --> ./nips/data\XC129590 - Great Spotted Woodpecker - Dendrocopos major.mp3
6109900  --> ./nips/data\XC129594 - Common Blackbird - Turdus merula.mp3
434499  --> ./nips/data\XC129595 - Eurasian Jay - Garrulus glandarius.mp3
453639  --> ./nips/data\XC129597 - Common Blackbird - Turdus merula.mp3
604106  --> ./nips/data\XC129598 - Eurasian Nuthatch - Sitta europaea.mp3
447856  --> ./nips/data\XC129599 - Great Spotted Woodpecker - Dendrocopos major.mp3
3074356  --> ./nips/data\XC129609 - Eurasian Blue Tit - Cyanistes caeruleus.mp3
1302173  --> ./nips/data\XC129612 - Coal Tit - Periparus ater.mp3
0  --> ./nips/data\XC129613 - Common Nightingale - Luscinia megarhynchos.mp3
291901  --> ./nips/data\XC129615 - Eurasian Jay - Garrulus glandarius.mp3
377905  --> ./nips/data\XC129622 - Great Tit - Parus major.mp3
2394364  --> ./nips/data\XC1296

679321  --> ./nips/data\XC133155 - Common Chiffchaff - Phylloscopus collybita.mp3
762466  --> ./nips/data\XC133160 - Common Chiffchaff - Phylloscopus collybita.mp3
601731  --> ./nips/data\XC133163 - Eurasian Blackcap - Sylvia atricapilla.mp3
1630733  --> ./nips/data\XC133209 - Coal Tit - Periparus ater.mp3
0  --> ./nips/data\XC133236 - Common Nightingale - Luscinia megarhynchos.mp3
0  --> ./nips/data\XC133262 - House Sparrow - Passer domesticus.mp3
139078  --> ./nips/data\XC133267 - Great Tit - Parus major.mp3
739162  --> ./nips/data\XC133270 - Great Spotted Woodpecker - Dendrocopos major.mp3
3468496  --> ./nips/data\XC133372 - Eurasian Blackcap - Sylvia atricapilla.mp3
1421787  --> ./nips/data\XC133374 - Eurasian Blue Tit - Cyanistes caeruleus.mp3
1522416  --> ./nips/data\XC133375 - Common Chiffchaff - Phylloscopus collybita.mp3
1043208  --> ./nips/data\XC133379 - Coal Tit - Periparus ater.mp3
351324  --> ./nips/data\XC133407 - European Robin - Erithacus rubecula.mp3
394707  --> ./nip

...

926577  --> ./nips/data\XC728692 - Great Spotted Woodpecker - Dendrocopos major.mp3
3091620  --> ./nips/data\XC728696 - Song Thrush - Turdus philomelos.mp3
585904  --> ./nips/data\XC728835 - Common Chiffchaff - Phylloscopus collybita.mp3
0  --> ./nips/data\XC728840 - Common Nightingale - Luscinia megarhynchos.mp3
3007729  --> ./nips/data\XC728842 - Great Tit - Parus major.mp3
2727792  --> ./nips/data\XC728851 - Song Thrush - Turdus philomelos.mp3
0  --> ./nips/data\XC728871 - Common Nightingale - Luscinia megarhynchos.mp3
8073568  --> ./nips/data\XC728872 - Eurasian Blackcap - Sylvia atricapilla.mp3
0  --> ./nips/data\XC728873 - Common Nightingale - Luscinia megarhynchos.mp3
439545  --> ./nips/data\XC728880 - Eurasian Blackcap - Sylvia atricapilla.mp3
5904763  --> ./nips/data\XC728927 - Song Thrush - Turdus philomelos.mp3
0  --> ./nips/data\XC728980 - European Robin - Erithacus rubecula.mp3
756082  --> ./nips/data\XC728981 - European Robin - Erithacus rubecula.mp3
1628633  --> ./nips/d

1907405  --> ./nips/data\XC736111 - Great Tit - Parus major.mp3
1717023  --> ./nips/data\XC736113 - European Robin - Erithacus rubecula.mp3
0  --> ./nips/data\XC736147 - European Robin - Erithacus rubecula.mp3
2056581  --> ./nips/data\XC736183 - Common Chiffchaff - Phylloscopus collybita.mp3
2378128  --> ./nips/data\XC736200 - Song Thrush - Turdus philomelos.mp3
559496  --> ./nips/data\XC736232 - Song Thrush - Turdus philomelos.mp3
176006  --> ./nips/data\XC736342 - Common Chiffchaff - Phylloscopus collybita.mp3
1101642  --> ./nips/data\XC736351 - Eurasian Jay - Garrulus glandarius.mp3
3488436  --> ./nips/data\XC736408 - Eurasian Blackcap - Sylvia atricapilla.mp3
341430  --> ./nips/data\XC736435 - Eurasian Wren - Troglodytes troglodytes.mp3
808006  --> ./nips/data\XC736476 - Eurasian Blackcap - Sylvia atricapilla.mp3
452829  --> ./nips/data\XC736478 - Eurasian Blackcap - Sylvia atricapilla.mp3
1536543  --> ./nips/data\XC736511 - Song Thrush - Turdus philomelos.mp3
119509  --> ./nips/da

121589  --> ./nips/data\XC744164 - Great Tit - Parus major.mp3
0  --> ./nips/data\XC744180 - House Sparrow - Passer domesticus.mp3
136130  --> ./nips/data\XC744190 - Coal Tit - Periparus ater.mp3
1035410  --> ./nips/data\XC744195 - Eurasian Blackcap - Sylvia atricapilla.mp3
1386653  --> ./nips/data\XC744196 - Common Chiffchaff - Phylloscopus collybita.mp3
3993922  --> ./nips/data\XC744202 - Eurasian Blackcap - Sylvia atricapilla.mp3
5967355  --> ./nips/data\XC744255 - Common Blackbird - Turdus merula.mp3
2557869  --> ./nips/data\XC744377 - Common Blackbird - Turdus merula.mp3
99403  --> ./nips/data\XC744696 - Coal Tit - Periparus ater.mp3
2746437  --> ./nips/data\XC744880 - Common Blackbird - Turdus merula.mp3
618344  --> ./nips/data\XC744883 - Eurasian Blackcap - Sylvia atricapilla.mp3
1178275  --> ./nips/data\XC744893 - Eurasian Blackcap - Sylvia atricapilla.mp3
208095  --> ./nips/data\XC744900 - Eurasian Blackcap - Sylvia atricapilla.mp3
531352  --> ./nips/data\XC744911 - Common Chi

980196  --> ./nips/data\XC90001 - Eurasian Blackcap - Sylvia atricapilla.mp3
1104002  --> ./nips/data\XC90002 - Eurasian Blackcap - Sylvia atricapilla.mp3
695271  --> ./nips/data\XC90003 - Eurasian Blackcap - Sylvia atricapilla.mp3
1639923  --> ./nips/data\XC90117 - Common Blackbird - Turdus merula.mp3
682013  --> ./nips/data\XC90166 - Eurasian Wren - Troglodytes troglodytes.mp3
491392  --> ./nips/data\XC90168 - Eurasian Wren - Troglodytes troglodytes.mp3
730335  --> ./nips/data\XC90217 - Common Chiffchaff - Phylloscopus collybita.mp3
730704  --> ./nips/data\XC90218 - Common Chiffchaff - Phylloscopus collybita.mp3
745833  --> ./nips/data\XC90219 - Common Chiffchaff - Phylloscopus collybita.mp3
647741  --> ./nips/data\XC90220 - Common Chiffchaff - Phylloscopus collybita.mp3
1214502  --> ./nips/data\XC90221 - Common Chiffchaff - Phylloscopus collybita.mp3
810424  --> ./nips/data\XC90255 - Song Thrush - Turdus philomelos.mp3
1474771  --> ./nips/data\XC90271 - Coal Tit - Periparus ater.mp3

566566  --> ./nips/data\XC96948 - Eurasian Jay - Garrulus glandarius.mp3
1688238  --> ./nips/data\XC96950 - Great Spotted Woodpecker - Dendrocopos major.mp3
1709224  --> ./nips/data\XC96951 - Great Spotted Woodpecker - Dendrocopos major.mp3
854008  --> ./nips/data\XC96952 - Eurasian Blue Tit - Cyanistes caeruleus.mp3
401369  --> ./nips/data\XC96980 - Great Tit - Parus major.mp3
374240  --> ./nips/data\XC96981 - Great Tit - Parus major.mp3
1211577  --> ./nips/data\XC96982 - Great Tit - Parus major.mp3
1720480  --> ./nips/data\XC96983 - Great Tit - Parus major.mp3
2327062  --> ./nips/data\XC97108 - Eurasian Wren - Troglodytes troglodytes.mp3
1806745  --> ./nips/data\XC97110 - Eurasian Nuthatch - Sitta europaea.mp3
1628966  --> ./nips/data\XC97112 - Song Thrush - Turdus philomelos.mp3
2447061  --> ./nips/data\XC97115 - Common Chiffchaff - Phylloscopus collybita.mp3
2729592  --> ./nips/data\XC97117 - Song Thrush - Turdus philomelos.mp3
2526716  --> ./nips/data\XC97120 - Great Tit - Parus m

In [59]:
files = mini_file_df["filename"]
for filename in tqdm(files):
    try:
        mini_file_df.loc[mini_file_df["filename"]== filename, "DONE"] = os.stat("./nips/data/" +  filename).st_size > 0
    except:
        continue

100%|████████████████████████████████████████████████████████████████████████████| 43210/43210 [07:31<00:00, 95.64it/s]


In [60]:
to_be_done = mini_file_df[~mini_file_df["DONE"]]


In [61]:
to_be_done.shape[0]

6767

In [62]:
mini_file_df.shape[0]

43210

In [1]:
from tqdm import tqdm
from time import sleep
for i, row in tqdm(to_be_done.iterrows()):
    try:
        row["download_path"] = download_by_url(row, "./nips/data/")
        mini_file_df.loc[i] = row
    except Exception as e:
        print("========================")
        print(e)
        continue
mini_file_df

NameError: name 'to_be_done' is not defined